# 端到端模型优化样例

参考：[e2e_opt_model](https://tvm.apache.org/docs/how_to/tutorials/e2e_opt_model.html)

本教程展示了如何使用 Apache TVM 来优化机器学习模型。使用来自 PyTorch 的预训练 ResNet-18 模型，并利用 TVM 的 Relax API 对其进行端到端的优化。请注意，默认的端到端优化可能不适合复杂的模型。

## 准备阶段

首先，准备模型和输入信息。使用来自PyTorch的预训练ResNet-18模型。

In [1]:
import set_env

In [2]:
import os
import numpy as np
import torch
from torch import fx
from torchvision.models.resnet import ResNet18_Weights, resnet18

torch_model = resnet18(weights=ResNet18_Weights.DEFAULT)

## 整体流程概述

```{figure} https://raw.githubusercontent.com/tlc-pack/web-data/main/images/design/tvm_overall_flow.svg
:align: center
:width: 80%
```

整体流程包括以下步骤：

- **构建或导入模型**：构建一个神经网络模型，或者从其他框架（如 PyTorch、ONNX）导入预训练的模型，并创建 TVM IRModule，其中包含编译所需的所有信息，包括用于计算图的高级别 Relax 函数和用于张量程序的低级 TensorIR 函数。
- **执行可组合优化**：执行一系列优化转换，例如图优化、张量程序优化和库调度。
- **构建和通用部署**：将优化后的模型构建为可在通用运行时部署的模块，并在不同设备上执行，如 CPU、GPU 或其他加速器。

## 将模型转换为 IRModule

使用 Relax 前端（面向 PyTorch）将模型转换为 IRModule，以便进一步优化。除了模型外，我们还需要提供输入的形状和数据类型。

In [3]:
import tvm
from tvm import relax
from tvm.relax.frontend.torch import from_fx

torch_model = resnet18(weights=ResNet18_Weights.DEFAULT)

# Give the input shape and data type
input_info = [((1, 3, 224, 224), "float32")]

# Convert the model to IRModule
with torch.no_grad():
    torch_fx_model = fx.symbolic_trace(torch_model)
    mod = from_fx(torch_fx_model, input_info, keep_params_as_input=True)

mod, params = relax.frontend.detach_params(mod)
mod.show()

## IRModule 优化

Apache TVM 提供了一个灵活的方式来优化 IRModule。围绕 IRModule 优化的所有运算都可以与现有的流水线组合。注意，每个转换都可以通过 ``tvm.ir.transform.Sequential`` 组合成一个优化流水线。

在本教程中，我们专注于通过自动调优（auto-tuning）对模型进行端到端优化。我们利用 MetaSchedule 调优模型，并将调优日志存储到数据库。我们还应用数据库到模型以获得最佳性能。

In [ ]:
TOTAL_TRIALS = 8000  # Change to 20000 for better performance if needed
target = tvm.target.Target("nvidia/geforce-rtx-3090-ti")  # Change to your target device
work_dir = "tuning_logs"

# Skip running in CI environment
IS_IN_CI = os.getenv("CI", "") == "true"
if not IS_IN_CI:
    with target:
        mod = tvm.ir.transform.Sequential(
            [
                # Convert BatchNorm into a sequence of simpler ops for fusion
                relax.transform.DecomposeOpsForInference(),
                # Canonicalize the bindings
                relax.transform.CanonicalizeBindings(),
                # Run default optimization pipeline
                relax.get_pipeline("zero"),
                # Tune the model and store the log to database
                relax.transform.MetaScheduleTuneIRMod({}, work_dir, TOTAL_TRIALS),
                # Apply the database
                relax.transform.MetaScheduleApplyDatabase(work_dir),
            ]
        )(mod)

    # Only show the main function
    mod["main"].show()

## 构建和部署

最后，我们构建优化后的模型并将其部署到目标设备。

In [ ]:
if not IS_IN_CI:
    ex = relax.build(mod, target="cuda")
    dev = tvm.device("cuda", 0)
    vm = relax.VirtualMachine(ex, dev)
    # Need to allocate data and params on GPU device
    gpu_data = tvm.nd.array(np.random.rand(1, 3, 224, 224).astype("float32"), dev)
    gpu_params = [tvm.nd.array(p, dev) for p in params["main"]]
    gpu_out = vm["main"](gpu_data, *gpu_params).numpy()

    print(gpu_out.shape)